In [1]:
import os
import math
import rasterio
from rasterio.features import rasterize
from rasterio.transform import from_origin
import fiona
import pandas as pd
import geopandas as gpd
from rasterio import features
import numpy as np
import matplotlib.pyplot as plt
from shapely.geometry import Polygon, MultiPolygon
from constants import SHAPEFILE_PATH, PROJECT_PATH

In [2]:
study_boundary = gpd.read_file(SHAPEFILE_PATH)

river_shapefile = '/Users/romero61/../../capstone/pyforest/ml_data/infona_data/river_buffer/river_buffer.gpkg'

roads = '/Users/romero61/../../capstone/pyforest/ml_data/infona_data/dissolved_road/dissolved_road.gpkg'

lup = gpd.read_file('/Users/romero61/../../capstone/pyforest/ml_data/lup_subsets/lup_11.gpkg')

limits_11 = gpd.read_file('/Users/romero61/../../capstone/pyforest/ml_data/active_inactive_subsets/active_inactive_11.gpkg')

define the desired resolution and extent for your output rasters to match the tree cover and deforestation rasters.
 reproject the study_boundary to match the output CRS and update its total bounds:

In [3]:
study_boundary = study_boundary.to_crs(epsg=4326)
lup = lup.to_crs(epsg=4326)
output_crs = 'EPSG:4326'
output_extent = (-62.64186038139295, -25.354320073574613, -57.14929123970096, -19.287457970745013)
output_resolution = (0.00026949458523585647, -0.00026949458523585647)
study_boundary = study_boundary.to_crs(output_crs)
study_area_bounds = study_boundary.total_bounds
limits_11 = limits_11.to_crs(epsg=4326)

In [ ]:
np.lup.unique('grupo')

In [9]:
limits_11

id   put_id  anho_capa  estado cod_dpto cod_dist  year_inactive  \
0     1815.0  PUT1815     2010.0     0.0        Q        1         2014.0   
1      877.0  PUT0877     2006.0     0.0        Q        5         2015.0   
2     1062.0  PUT1062     2007.0     0.0        Q        1         2015.0   
3     2019.0  PUTSR21     2011.0     0.0        Q        1         2015.0   
4     1015.0  PUT1015     2006.0     0.0        Q        7         2016.0   
...      ...      ...        ...     ...      ...      ...            ...   
1544   104.0  PUT0104     2000.0     1.0        R        3         2023.0   
1545   105.0  PUT0105     2000.0     1.0        R        3         2023.0   
1546   107.0  PUT0107     2000.0     1.0        Q        1         2023.0   
1547   109.0  PUT0109     2000.0     1.0        Q        5         2023.0   
1548  1117.0  PUT1117     2000.0     1.0        Q        7         2023.0   

     to_putid   fecha_res    cat  \
0     PUT2618  2010-09-27  00001   
1     PUT2770  2006-08-23  00011   
2     PUT2690  2007-10-16  00014   
3     PUT2682  2011-09-12  00016   
4     PUT0565  2006-10-23  00018   
...       ...         ...    ...   
1544  PUT0104  2000-06-26  05320   
1545  PUT0105  2000-03-30  05321   
1546  PUT0107  2000-11-29  05322   
1547  PUT0109  2000-11-29  05354   
1548  PUT1117  2000-05-22  05358   

                                               geometry  
0     MULTIPOLYGON (((-60.80866 -20.92393, -60.80859...  
1     MULTIPOLYGON (((-59.98440 -21.76702, -60.05092...  
2     MULTIPOLYGON (((-61.95967 -22.07656, -61.95080...  
3     MULTIPOLYGON (((-60.97581 -21.75526, -60.97546...  
4     MULTIPOLYGON (((-61.60615 -22.91480, -61.60314...  
...                                                 ...  
1544  MULTIPOLYGON (((-59.77025 -22.05518, -59.77000...  
1545  MULTIPOLYGON (((-59.45157 -21.67045, -59.43344...  
1546  MULTIPOLYGON (((-60.49507 -22.39044, -60.45322...  
1547  MULTIPOLYGON (((-60.15977 -22.15421, -60.11739...  
1548  MULTIPOLYGON (((-60.59506 -22.75152, -60.51061...  

[1549 rows x 11 columns]

In [6]:
def extract_polygon_features(polygon):
    # Check if the input geometry is a Polygon or a MultiPolygon
    if isinstance(polygon, Polygon):
        largest_polygon = polygon
    elif isinstance(polygon, MultiPolygon):
        # For MultiPolygon, select the largest polygon by area
        largest_polygon = max(polygon.geoms, key=lambda x: x.area)
    else:
        raise ValueError("Unsupported geometry type")

    # Calculate the number of sides for the largest polygon
    num_sides = len(largest_polygon.exterior.coords) - 1

    # Calculate the bounding box and aspect ratio for the largest polygon
    minx, miny, maxx, maxy = largest_polygon.bounds
    width = maxx - minx
    height = maxy - miny
    aspect_ratio = width / height

    # Calculate the area and perimeter for the largest polygon
    area = largest_polygon.area
    perimeter = largest_polygon.length

    # Calculate the compactness for the largest polygon
    compactness = (4 * math.pi * area) / (perimeter ** 2)

    # Return the calculated features as a dictionary
    return {
        'num_sides': num_sides,
        'aspect_ratio': aspect_ratio,
        'area': area,
        'perimeter': perimeter,
        'compactness': compactness
    }

In [7]:
# Apply the extract_polygon_features function to the 'geometry' column
extracted_features = lup['geometry'].apply(extract_polygon_features)

# Convert the resulting Series of dictionaries to a DataFrame
features_df = pd.DataFrame(extracted_features.tolist())

# Reset index of the lup DataFrame and drop the old index column
lup.reset_index(drop=True, inplace=True)

# Concatenate the DataFrames along axis 1 (columns)
lup_with_features = pd.concat([lup, features_df], axis=1)



This function reads an input vector file (GeoPackage or Shapefile), converts the attribute column to numerical values or sets it to a single value if provided, and prepares the metadata for creating an output raster file.

input_vector: The path to the input vector file (GeoPackage or Shapefile).

output_raster: The path to the output raster file.

attribute: The name of the attribute column in the input vector file that should be used as the pixel value in the output raster.

study_area_bounds: The bounds of the study area as a tuple (minx, miny, maxx, maxy).

single_value (optional, default: None): If provided, all the features in the input vector will be encoded with this single value in the output raster. If not provided, the attribute column values will be used.

resolution: output raster generated from the vector_to_raster function will match the resolution and extent of the Hansen dataset.

dtype (optional, default: 'uint16'): The data type of the output raster pixel values.


In [6]:
def vector_to_raster(input_vector, output_raster, attribute, study_area_bounds, single_value=None, resolution=(abs(0.00026949458523585647), abs(-0.00026949458523585647)), dtype='uint16'):
    # Check if input_vector is a GeoDataFrame or a file path
    if isinstance(input_vector, gpd.GeoDataFrame):
        gdf = input_vector
    else:
        # Read the input vector file (GeoPackage or Shapefile) into a GeoDataFrame
        gdf = gpd.read_file(input_vector)

    gdf[attribute] = gdf[attribute].astype(str)

   # If single_value is None, convert the attribute column to numerical values
    # If single_value is provided, set the attribute column to the provided single_value
    if single_value is None:
        unique_values = np.unique(gdf[attribute])
        print(f"Unique values for {attribute}:")
        value_mapping = {value: idx for idx, value in enumerate(unique_values)}
        for value in unique_values:
            print(f"{value}: {value_mapping[value]}")
        gdf[attribute] = gdf[attribute].replace(value_mapping).astype(dtype)
    else:
        gdf[attribute] = single_value

    # Use the study area bounds to define the dimensions and transform of the output raster
    minx, miny, maxx, maxy = study_area_bounds
    width = int(np.ceil((maxx - minx) / abs(resolution[0])))
    height = int(np.ceil((maxy - miny) / abs(resolution[1])))
    out_transform = rasterio.transform.from_bounds(minx, miny, maxx, maxy, width, height)


    # Define the metadata for the output raster file
    out_meta = {
        'driver': 'GTiff',
        'width': width,
        'height': height,
        'count': 1,
        'dtype': dtype,
        'crs': 'EPSG:4326',
        'transform': out_transform
    }
    
    # Open the output raster file for writing with the specified metadata
    with rasterio.open(output_raster, 'w', **out_meta) as dst:
        # Create a generator of tuples containing the geometry and attribute value for each feature in the input vector data
        shapes = ((geom, value) for geom, value in zip(gdf['geometry'], gdf[attribute]))
        
        # Burn the geometries and their corresponding attribute values into a raster array
        burned = features.rasterize(
            shapes=shapes,         # The generator of geometry-attribute tuples
            fill=0,                # The default value for pixels not covered by any geometry
            out_shape=(height, width), # The shape of the output raster array (number of rows and columns)
            transform=out_transform,   # The affine transformation matrix that maps pixel coordinates to the coordinate reference system
            dtype=dtype            # The data type of the raster array
        )
        
        # Write the burned raster array to the output raster file
        dst.write(burned, 1)

In [7]:
def process_columns(input_vector, output_dir, study_area_bounds, resolution,columns=None, single_value=None):
    if columns is None:
        gdf = gpd.read_file(input_vector)
        columns = gdf.columns.drop(['geometry'])

    for column in columns:
        output_raster = f"{output_dir}/{column}_raster.tif"
        vector_to_raster(input_vector, output_raster, column, study_area_bounds, single_value=single_value)

In [8]:
output_dir = os.path.join(PROJECT_PATH,'data_loading/outputs')

In [37]:

process_columns(lup, output_dir, study_area_bounds, columns=['grupo'], resolution=output_resolution)


Unique values for grupo:
AREA_AUTORIZADA: 0
BOSQUES: 1
EN_CONFLICTO: 2
OTRAS_COBERTURAS: 3
OTRAS_TIERRAS_FORESTALES: 4
nan: 5


In [11]:
lup_with_features.columns

Index(['id', 'put_id', 'categoria_ant', 'grupo', 'categoria', 'geometry',
       'num_sides', 'aspect_ratio', 'area', 'perimeter', 'compactness'],
      dtype='object')

In [12]:
process_columns(lup_with_features, output_dir, study_area_bounds, columns=['categoria_ant','categoria', 
       'num_sides', 'aspect_ratio', 'area', 'perimeter', 'compactness'], resolution=output_resolution)


Unique values for categoria_ant:
A-FORESTAR: 0
A-HABILITAR: 1
A-REFORESTAR: 2
A-REGENERAR: 3
AREA AFECTADA POR M*: 4
B-INUNDABLE: 5
BOSQUETES: 6
CAMINO: 7
EN-CONFLICTO: 8
FORESTACION: 9
FRANJAS: 10
MANEJO-FORESTAL: 11
MATORRAL: 12
NO_FORESTAL: 13
PALMARES: 14
PASTO: 15
PROTECCION: 16
PROTECCION-CAUCES: 17
REFORESTACION: 18
REGENERACION: 19
REMANENTE: 20
RESERVA-FORESTAL: 21
SIN COBERTURA: 22
nan: 23
Unique values for categoria:
BOSQUETES: 0
BOSQUE_CAUCES: 1
BOSQUE_EXCEDENTE: 2
BOSQUE_FRANJAS: 3
MATORRALES: 4
PALMARES: 5
PASTIZALES: 6
RESERVA_LEGAL: 7
nan: 8
Unique values for num_sides:
10: 0
100: 1
1001: 2
1005: 3
101: 4
102: 5
1026: 6
103: 7
104: 8
1042: 9
1045: 10
1049: 11
105: 12
106: 13
1068: 14
107: 15
108: 16
1083: 17
109: 18
11: 19
110: 20
1103: 21
1104: 22
111: 23
112: 24
1121: 25
113: 26
1135: 27
1136: 28
114: 29
115: 30
1157: 31
1159: 32
116: 33
1169: 34
117: 35
1173: 36
118: 37
1185: 38
119: 39
1195: 40
12: 41
120: 42
121: 43
122: 44
1221: 45
123: 46
1233: 47
124: 48
1245: 4

In [ ]:
process_columns(limits_11, output_dir, study_area_bounds, columns=['put_id'], resolution=output_resolution)
